# Incidence of influenza-like illness in France

In [2]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
import isoweek

The data on the incidence of influenza-like illness are available from the Web site of the [Réseau Sentinelles](http://www.sentiweb.fr/). We download them as a file in CSV format, in which each line corresponds to a week in the observation period. Only the complete dataset, starting in 1984 and ending with a recent week, is available for download.

In [3]:
data_url = "http://www.sentiweb.fr/datasets/incidence-PAY-3.csv"

This is the documentation of the data from [the download site](https://ns.sentiweb.fr/incidence/csv-schema-v1.json):

| Column name  | Description                                                                                                               |
|--------------|---------------------------------------------------------------------------------------------------------------------------|
| `week`       | ISO8601 Yearweek number as numeric (year times 100 + week nubmer)                                                               |
| `indicator`  | Unique identifier of the indicator, see metadata document https://www.sentiweb.fr/meta.json                               |
| `inc`        | Estimated incidence value for the time step, in the geographic level                                                      |
| `inc_low`    | Lower bound of the estimated incidence 95% Confidence Interval                                                            |
| `inc_up`     | Upper bound of the estimated incidence 95% Confidence Interval                                                            |
| `inc100`     | Estimated rate incidence per 100,000 inhabitants                                                                          |
| `inc100_low` | Lower bound of the estimated incidence 95% Confidence Interval                                                            |
| `inc100_up`  | Upper bound of the estimated rate incidence 95% Confidence Interval                                                       |
| `geo_insee`  | Identifier of the geographic area, from INSEE https://www.insee.fr                                                        |
| `geo_name`   | Geographic label of the area, corresponding to INSEE code. This label is not an id and is only provided for human reading |

The first line of the CSV file is a comment, which we ignore with `skip=1`.

In order to protect us in case the Réseau Sentinelles Web server disappears or is modified, we make a local copy of this dataset that we store together with our analysis. It is unnecessary and even risky to download the data at each execution, because in case of a malfunction we might be replacing our file by a corrupted version. Therefore we download the data only if no local copy exists.

In [4]:
data_file = "syndrome-grippal.csv"

import os
import urllib.request
if not os.path.exists(data_file):
    urllib.request.urlretrieve(data_url, data_file)

In [6]:
raw_data = pd.read_csv(data_file, skiprows=1)
raw_data

week  indicator     inc   inc_low    inc_up inc100  inc100_low  \
0     202328          3   10829    5995.0   15663.0     16         9.0   
1     202327          3    9197    5864.0   12530.0     14         9.0   
2     202326          3    9023    5934.0   12112.0     14         9.0   
3     202325          3   10090    6739.0   13441.0     15        10.0   
4     202324          3   11308    7639.0   14977.0     17        11.0   
5     202323          3   14300   10661.0   17939.0     22        17.0   
6     202322          3   18303   13822.0   22784.0     28        21.0   
7     202321          3   16460   12188.0   20732.0     25        19.0   
8     202320          3   16162   11963.0   20361.0     24        18.0   
9     202319          3   16901   12577.0   21225.0     25        18.0   
10    202318          3   19929   15402.0   24456.0     30        23.0   
11    202317          3   27007   21779.0   32235.0     41        33.0   
12    202316          3   27875   22767.0   32983.0     42        34.0   
13    202315          3   37455   30993.0   43917.0     56        46.0   
14    202314          3   48060   40671.0   55449.0     72        61.0   
15    202313          3   64859   56800.0   72918.0     98        86.0   
16    202312          3   72750   64499.0   81001.0    109        97.0   
17    202311          3   74638   66420.0   82856.0    112       100.0   
18    202310          3   76368   68243.0   84493.0    115       103.0   
19    202309          3   62062   54778.0   69346.0     93        82.0   
20    202308          3   76391   68065.0   84717.0    115       102.0   
21    202307          3   89851   80397.0   99305.0    135       121.0   
22    202306          3   97368   87636.0  107100.0    146       131.0   
23    202305          3   95469   86268.0  104670.0    144       130.0   
24    202304          3   74901   66916.0   82886.0    113       101.0   
25    202303          3   69570   61893.0   77247.0    105        93.0   
26    202302          3   78260   70090.0   86430.0    118       106.0   
27    202301          3  121773  111024.0  132522.0    183       167.0   
28    202252          3  155371  142004.0  168738.0    234       214.0   
29    202251          3  248319  232128.0  264510.0    374       350.0   
...      ...        ...     ...       ...       ...    ...         ...   
1990  198521          3   26096   19621.0   32571.0     47        35.0   
1991  198520          3   27896   20885.0   34907.0     51        38.0   
1992  198519          3   43154   32821.0   53487.0     78        59.0   
1993  198518          3   40555   29935.0   51175.0     74        55.0   
1994  198517          3   34053   24366.0   43740.0     62        44.0   
1995  198516          3   50362   36451.0   64273.0     91        66.0   
1996  198515          3   63881   45538.0   82224.0    116        83.0   
1997  198514          3  134545  114400.0  154690.0    244       207.0   
1998  198513          3  197206  176080.0  218332.0    357       319.0   
1999  198512          3  245240  223304.0  267176.0    445       405.0   
2000  198511          3  276205  252399.0  300011.0    501       458.0   
2001  198510          3  353231  326279.0  380183.0    640       591.0   
2002  198509          3  369895  341109.0  398681.0    670       618.0   
2003  198508          3  389886  359529.0  420243.0    707       652.0   
2004  198507          3  471852  432599.0  511105.0    855       784.0   
2005  198506          3  565825  518011.0  613639.0   1026       939.0   
2006  198505          3  637302  592795.0  681809.0   1155      1074.0   
2007  198504          3  424937  390794.0  459080.0    770       708.0   
2008  198503          3  213901  174689.0  253113.0    388       317.0   
2009  198502          3   97586   80949.0  114223.0    177       147.0   
2010  198501          3   85489   65918.0  105060.0    155       120.0   
2011  198452          3   84830   60602.0  109058.0    154       110.0   
2012  198451

Are there missing data points? Yes, week 19 of year 1989 does not have any observed values.

In [7]:
raw_data[raw_data.isnull().any(axis=1)]

week  indicator inc  inc_low  inc_up inc100  inc100_low  inc100_up  \
1783  198919          3   -      NaN     NaN      -         NaN        NaN   

     geo_insee geo_name  
1783        FR   France

We delete this point, which does not have big consequence for our rather simple analysis.

In [8]:
data = raw_data.dropna().copy()
data

week  indicator     inc   inc_low    inc_up inc100  inc100_low  \
0     202328          3   10829    5995.0   15663.0     16         9.0   
1     202327          3    9197    5864.0   12530.0     14         9.0   
2     202326          3    9023    5934.0   12112.0     14         9.0   
3     202325          3   10090    6739.0   13441.0     15        10.0   
4     202324          3   11308    7639.0   14977.0     17        11.0   
5     202323          3   14300   10661.0   17939.0     22        17.0   
6     202322          3   18303   13822.0   22784.0     28        21.0   
7     202321          3   16460   12188.0   20732.0     25        19.0   
8     202320          3   16162   11963.0   20361.0     24        18.0   
9     202319          3   16901   12577.0   21225.0     25        18.0   
10    202318          3   19929   15402.0   24456.0     30        23.0   
11    202317          3   27007   21779.0   32235.0     41        33.0   
12    202316          3   27875   22767.0   32983.0     42        34.0   
13    202315          3   37455   30993.0   43917.0     56        46.0   
14    202314          3   48060   40671.0   55449.0     72        61.0   
15    202313          3   64859   56800.0   72918.0     98        86.0   
16    202312          3   72750   64499.0   81001.0    109        97.0   
17    202311          3   74638   66420.0   82856.0    112       100.0   
18    202310          3   76368   68243.0   84493.0    115       103.0   
19    202309          3   62062   54778.0   69346.0     93        82.0   
20    202308          3   76391   68065.0   84717.0    115       102.0   
21    202307          3   89851   80397.0   99305.0    135       121.0   
22    202306          3   97368   87636.0  107100.0    146       131.0   
23    202305          3   95469   86268.0  104670.0    144       130.0   
24    202304          3   74901   66916.0   82886.0    113       101.0   
25    202303          3   69570   61893.0   77247.0    105        93.0   
26    202302          3   78260   70090.0   86430.0    118       106.0   
27    202301          3  121773  111024.0  132522.0    183       167.0   
28    202252          3  155371  142004.0  168738.0    234       214.0   
29    202251          3  248319  232128.0  264510.0    374       350.0   
...      ...        ...     ...       ...       ...    ...         ...   
1990  198521          3   26096   19621.0   32571.0     47        35.0   
1991  198520          3   27896   20885.0   34907.0     51        38.0   
1992  198519          3   43154   32821.0   53487.0     78        59.0   
1993  198518          3   40555   29935.0   51175.0     74        55.0   
1994  198517          3   34053   24366.0   43740.0     62        44.0   
1995  198516          3   50362   36451.0   64273.0     91        66.0   
1996  198515          3   63881   45538.0   82224.0    116        83.0   
1997  198514          3  134545  114400.0  154690.0    244       207.0   
1998  198513          3  197206  176080.0  218332.0    357       319.0   
1999  198512          3  245240  223304.0  267176.0    445       405.0   
2000  198511          3  276205  252399.0  300011.0    501       458.0   
2001  198510          3  353231  326279.0  380183.0    640       591.0   
2002  198509          3  369895  341109.0  398681.0    670       618.0   
2003  198508          3  389886  359529.0  420243.0    707       652.0   
2004  198507          3  471852  432599.0  511105.0    855       784.0   
2005  198506          3  565825  518011.0  613639.0   1026       939.0   
2006  198505          3  637302  592795.0  681809.0   1155      1074.0   
2007  198504          3  424937  390794.0  459080.0    770       708.0   
2008  198503          3  213901  174689.0  253113.0    388       317.0   
2009  198502          3   97586   80949.0  114223.0    177       147.0   
2010  198501          3   85489   65918.0  105060.0    155       120.0   
2011  198452          3   84830   60602.0  109058.0    154       110.0   
2012  198451

Our dataset uses an uncommon encoding; the week number is attached
to the year number, leaving the impression of a six-digit integer.
That is how Pandas interprets it.

A second problem is that Pandas does not know about week numbers.
It needs to be given the dates of the beginning and end of the week.
We use the library `isoweek` for that.

Since the conversion is a bit lengthy, we write a small Python 
function for doing it. Then we apply it to all points in our dataset. 
The results go into a new column 'period'.

In [9]:
def convert_week(year_and_week_int):
    year_and_week_str = str(year_and_week_int)
    year = int(year_and_week_str[:4])
    week = int(year_and_week_str[4:])
    w = isoweek.Week(year, week)
    return pd.Period(w.day(0), 'W')

data['period'] = [convert_week(yw) for yw in data['week']]

There are two more small changes to make.

First, we define the observation periods as the new index of
our dataset. That turns it into a time series, which will be
convenient later on.

Second, we sort the points chronologically.

In [10]:
sorted_data = data.set_index('period').sort_index()

We check the consistency of the data. Between the end of a period and
the beginning of the next one, the difference should be zero, or very small.
We tolerate an error of one second.

This is OK except for one pair of consecutive periods between which
a whole week is missing.

We recognize the dates: it's the week without observations that we
have deleted earlier!

In [11]:
periods = sorted_data.index
for p1, p2 in zip(periods[:-1], periods[1:]):
    delta = p2.to_timestamp() - p1.end_time
    if delta > pd.Timedelta('1s'):
        print(p1, p2)

1989-05-01/1989-05-07 1989-05-15/1989-05-21


A first look at the data!

In [12]:
sorted_data['inc'].plot()

TypeError: Empty 'DataFrame': no numeric data to plot

A zoom on the last few years shows more clearly that the peaks are situated in winter.

In [ ]:
sorted_data['inc'][-200:].plot()

## Study of the annual incidence

Since the peaks of the epidemic happen in winter, near the transition
between calendar years, we define the reference period for the annual
incidence from August 1st of year $N$ to August 1st of year $N+1$. We
label this period as year $N+1$ because the peak is always located in
year $N+1$. The very low incidence in summer ensures that the arbitrariness
of the choice of reference period has no impact on our conclusions.

Our task is a bit complicated by the fact that a year does not have an
integer number of weeks. Therefore we modify our reference period a bit:
instead of August 1st, we use the first day of the week containing August 1st.

A final detail: the dataset starts in October 1984, the first peak is thus
incomplete, We start the analysis with the first full peak.

In [ ]:
first_august_week = [pd.Period(pd.Timestamp(y, 8, 1), 'W')
                     for y in range(1985,
                                    sorted_data.index[-1].year)]

Starting from this list of weeks that contain August 1st, we obtain intervals of approximately one year as the periods between two adjacent weeks in this list. We compute the sums of weekly incidences for all these periods.

We also check that our periods contain between 51 and 52 weeks, as a safeguard against potential mistakes in our code.

In [ ]:
year = []
yearly_incidence = []
for week1, week2 in zip(first_august_week[:-1],
                        first_august_week[1:]):
    one_year = sorted_data['inc'][week1:week2-1]
    assert abs(len(one_year)-52) < 2
    yearly_incidence.append(one_year.sum())
    year.append(week2.year)
yearly_incidence = pd.Series(data=yearly_incidence, index=year)

And here are the annual incidences.

In [ ]:
yearly_incidence.plot(style='*')

A sorted list makes it easier to find the highest values (at the end).

In [ ]:
yearly_incidence.sort_values()

Finally, a histogram clearly shows the few very strong epidemics, which affect about 10% of the French population,
but are rare: there were three of them in the course of 35 years. The typical epidemic affects only half as many people.

In [ ]:
yearly_incidence.hist(xrot=20)